In [1]:
import pandas as pd
import altair as alt

from vega_datasets import data


alt.data_transformers.disable_max_rows()

df = pd.read_csv('EU-UK-Weather-Data.csv')
df.columns

Index(['country', 'location_name', 'latitude', 'longitude',
       'temperature_celsius', 'humidity', 'air_quality_Ozone', 'date', 'day',
       'month', 'year', 'week', 'time', 'season', 'condition'],
      dtype='object')

In [2]:
HEIGHT, WIDTH = 800, 500

map_source = alt.topo_feature(data.world_110m.url, 'countries')
map_brush = alt.selection_interval(
    # value={'longitude': [-3, 3], 'latitude': [50, 55]}  # this crops the final chart ?
)
line_chart_scale = alt.selection_interval(bind='scales', encodings=['x'])
city_selection = alt.selection_point(fields=['location_name'], bind='legend')

base = alt.layer(
    alt.Chart(map_source).mark_geoshape(fill='lightgray', stroke='gray')
).properties(
    width=WIDTH,
    height=HEIGHT,
    projection={
        'type': 'azimuthalEqualArea',
        'rotate': [-10, -52],
        'translate': [WIDTH//2, HEIGHT//2],
        'scale': 700,
        'precision': 0.1
})
city_points = alt.Chart(df).mark_circle(size=50).encode(
    latitude=alt.X('latitude:Q'),
    longitude=alt.Y('longitude:Q'),
    color=alt.Color('location_name:N', title='City', legend=alt.Legend(orient='left')),
    # opacity=alt.condition(map_brush, alt.value(1), alt.value(0.2)), # does not work on lat long
    tooltip=[alt.Tooltip('location_name', title='City'),
             alt.Tooltip('country', title='Country')],
).properties(
    title='Cities in Europe',
    width=WIDTH,
    height=HEIGHT
).add_params(
    map_brush,
    city_selection,
).transform_filter(
    city_selection,
)

base_line_chart = alt.Chart(df).mark_line(point=True).encode(
    x=alt.X('date:T', title=None),
    color=alt.Color('location_name:N', legend=None),
    shape=alt.Shape('condition:N', title='Condition', legend=alt.Legend(orient='right')),
).properties(
    width=WIDTH,
    height=0.3 * HEIGHT
).add_params(
    line_chart_scale,
).transform_filter(
    map_brush,
    line_chart_scale,
    city_selection,
)
base_line_tooltips = [alt.Tooltip('location_name', title='City'),
                      alt.Tooltip('date:T', title='Date'),
                      alt.Tooltip('condition', title='Condition'),]
temp_line = base_line_chart.encode(
    y=alt.Y('temperature_celsius:Q', title='Temperature (°C)'),
    tooltip=base_line_tooltips + [alt.Tooltip('temperature_celsius:Q', title='Temperature °C')]
)

humidity_line = base_line_chart.encode(
    y=alt.Y('humidity:Q', title='Humidity %'),
    tooltip=base_line_tooltips + [alt.Tooltip('humidity:Q', title='Humidity (%)')]
)
air_quality_line = base_line_chart.encode(
    x=alt.X('date:T', title='Date'),
    y=alt.Y('air_quality_Ozone:Q', title='Air Quality Ozone'),
    tooltip=base_line_tooltips + [alt.Tooltip('air_quality_Ozone:Q', title='Air Quality (Ozone)')]
)


systemA = ((base + city_points) |
           (temp_line & humidity_line & air_quality_line)
          ).properties(
              title='System A'
          )
systemA.save('systemA.html')
systemA

alt.HConcatChart(...)

## Tasks
1. Identify the week # that had the hottest temperatures in London, and what was the temperature.
2. Find 3 cities with ideal conditions (temp: 22 to 24, humidity: 40 to 50) in October.
3. Which city had the most humidity overall?
4. Determine the season when air quality was the best in Madrid.
5. Which city had the most sunny days in September 2024.

In [3]:
HEIGHT, WIDTH = 800, 500

map_source = alt.topo_feature(data.world_110m.url, 'countries')
map_brush = alt.selection_interval(
    value={'longitude': [-3, 3], 'latitude': [50, 55]}  # this crops the final chart ?
)
line_chart_scale = alt.selection_interval(bind='scales', encodings=['x'])
city_selection = alt.selection_point(fields=['location_name'], bind='legend')

base = alt.layer(
    alt.Chart(map_source).mark_geoshape(fill='lightgray', stroke='gray')
).properties(
    width=WIDTH,
    height=HEIGHT,
    projection={
        'type': 'azimuthalEqualArea',
        'rotate': [-10, -52],
        'translate': [WIDTH//2, HEIGHT//2],
        'scale': 700,
        'precision': 0.1
})
city_points = alt.Chart(df).mark_circle(size=50).encode(
    latitude=alt.X('latitude:Q'),
    longitude=alt.Y('longitude:Q'),
    color=alt.Color('location_name:N', title='City', legend=alt.Legend(orient='left')),
    # opacity=alt.condition(map_brush, alt.value(1), alt.value(0.2)), # does not work on lat long
    tooltip=[alt.Tooltip('location_name', title='City'),
             alt.Tooltip('country', title='Country')],
).properties(
    title='Cities in Europe',
    width=WIDTH,
    height=HEIGHT
).add_params(
    map_brush,
    city_selection,
).transform_filter(
    city_selection,
)
nearest = alt.selection_point(nearest=True, on='pointerover', fields=['date',], empty=False)

base_line_tooltips = [alt.Tooltip('location_name', title='City'),
                      alt.Tooltip('date:T', title='Date'),
                      alt.Tooltip('condition', title='Condition'),]
def create_line_chart(y_column, y_title):
    base = alt.Chart(df).mark_line().encode(
        x=alt.X("date:T", title=None),
        y=alt.Y(f"{y_column}:Q", title=y_title),
        color=alt.Color("location_name:N"),
        shape=alt.Shape('condition:N', title='Condition', legend=alt.Legend(orient='right')),
        tooltip=base_line_tooltips,
    ).add_params(
        line_chart_scale,
    ).transform_filter(
        map_brush,
        line_chart_scale,
        city_selection,
    )
    points = base.mark_point().encode(
        opacity=alt.condition(nearest, alt.value(1), alt.value(0)),
        shape=alt.Shape('condition:N', title='Condition', legend=alt.Legend(orient='right')),
    )
    text = base.mark_text(align="left", dx=5, dy=-5).encode(
        text=alt.condition(nearest, 'label:N', alt.value(""))
    ).transform_calculate(
        label=getattr(alt.datum, y_column)
    )
    selectors = alt.Chart(df).mark_point().encode(
        x="date:T",
        opacity=alt.value(0),
    ).add_params(nearest)
    rules = alt.Chart(df).mark_rule(color="gray").encode(
        x="date:T",
    ).transform_filter(
        nearest
    )
    date_text = alt.Chart(df).mark_text(align="center", dy=110, fontSize=12).encode(
        x="date:T",
        text=alt.Text("date:T", format="%Y-%m-%d")
    ).transform_filter(nearest)

    return alt.layer(base, points, text, rules, selectors, date_text).properties(
                        width=WIDTH,
                        height=0.3 * HEIGHT
)

temp_line = create_line_chart("temperature_celsius", "Temperature (°C)")
humidity_line = create_line_chart("humidity", "Humidity (%)")
air_quality_line = create_line_chart("air_quality_Ozone", "Air Quality (Ozone)")

systemA = ((base + city_points) |
           (temp_line & humidity_line & air_quality_line)
          ).properties(
              title='System A'
          )
# systemA.save('systemA.html')
systemA

alt.HConcatChart(...)